## Minimum path in BKK transportation map network

## Data preprocessing for BKK Network

In [7]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
from math import sin, cos, sqrt, atan2, radians
import random as rd
import pickle

### Parsing time data from string, and calculating difference

In [2]:
def calculate_time_difference(time1: str, time2: str) -> int:
    def convert_str_time_to_int(time: str) -> int:
        splitted_time = time.split(':')
        return int(splitted_time[2]) + int(splitted_time[1]) * 60 + int(splitted_time[0]) * 3600
    return convert_str_time_to_int(time= time2) - convert_str_time_to_int(time= time1) + 5

### Extracting coordinates from dataframe as float

In [3]:
def extract_coordinates(raw_lat, raw_lon):
    lat = round(float(raw_lat),6)
    lon = round(float(raw_lon),6)
    return (lon,lat)

### Measuring distance in meters between 2 coordinates

In [4]:
def calculate_distance_between_coordinates_in_meters(lat1: float, lon1: float, lat2: float, lon2: float):
    R = 6373.0
    dlat = radians(lat2 - lat1)
    dlon = radians(lon2 - lon1)
    a = (sin(dlat / 2) * sin(dlat / 2) +
         cos(radians(lat1)) * cos(radians(lat2)) *
         sin(dlon / 2) * sin(dlon / 2))
    c = 2 * atan2(sqrt(a), sqrt(1 - a))
    d = R * c
    return d * 1000

### Checking whether a node is close to a set of other nodes

In [5]:
def check_whether_node_isclose(nodes,new_node):
    threshold_in_meters = 500
    for node in nodes:
        if calculate_distance_between_coordinates_in_meters(new_node[1],new_node[2],node[1],node[2]) < threshold_in_meters:
            return True
    return False

### Reading datasets, and removing unnecessary columns

In [ ]:
stops = pd.read_csv('stops.txt', low_memory=False)
#pathways = pd.read_csv('pathways.txt', low_memory=False)
routes = pd.read_csv('routes.txt', low_memory=False)
trips = pd.read_csv('trips.txt', low_memory=False)
#shapes = pd.read_csv('shapes.txt', low_memory=False)
stop_times = pd.read_csv('stop_times.txt', low_memory=False)

In [ ]:
#Remove unnecessary columns
stops = stops[['stop_id','stop_name','stop_lat','stop_lon']]
trips = trips[['route_id','trip_id','direction_id']]
routes = routes[['route_id','route_short_name','route_desc','route_color']]
stop_times = stop_times[['trip_id','stop_id','arrival_time','departure_time']]

In [ ]:
stops.head()

In [ ]:
#Joining routes and trips
routes_info = pd.merge(trips, routes, on=['route_id'])
routes_info.head()

In [ ]:
#Joining stop_times and stops
detailed_stops = pd.merge(stops,stop_times, on=['stop_id'])
detailed_stops.head()

In [ ]:
#Joining all data together
dataset = pd.merge(routes_info,detailed_stops, on=['trip_id'])
dataset.head()

In [ ]:
#Get all unique trips
all_lines = dataset.trip_id.unique()
all_lines.shape

In [ ]:
#number of unique routes
all_routes = dataset.route_id.unique()
all_routes.shape

### Selecting only one service/day 

In [ ]:
# Getting unique trip_ids
unique_trip_ids = []

for route in all_routes:
    selected_route_df = (dataset.loc[dataset['route_id'] == str(route)]).sort_values('arrival_time')
    selected_route_df.reset_index(drop=True, inplace=True)
    all_trips = selected_route_df.trip_id.unique()
    
    #First service in the morning
    #unique_trip_ids.append(all_trips[0])
    
    #Service at the middle of the day
    #middle_of_the_day = len(all_trips) // 2
    #unique_trip_ids.append(all_trips[middle_of_the_day])
    
    #Last service at the evening
    #unique_trip_ids.append(all_trips[-1])
    
    #Randomly select
    unique_trip_ids.append(all_trips[rd.randint(0, len(all_trips)-1)])

### Generating dataset as input for the Graph

In [ ]:
def generate_data_for_network(dataframe):
    station_name_labels = {}
    station_name_labels[dataframe['stop_id'][0]] = [dataframe['stop_name'][0]][0]
    station_positions = {}
    lon,lat = extract_coordinates(dataframe['stop_lat'][0],dataframe['stop_lon'][0])
    station_positions[dataframe['stop_id'][0]] = (lon,lat)
    edges = []
    edge_labels = {}
    edge_colors = []
    
    node_labels = {}
    node_labels[dataframe['stop_id'][0]] = {'name': [dataframe['stop_name'][0]][0],'lon': lon,'lat': lat}
    
    for i in range(1,len(dataframe)):
        
        #Getting coordinates
        lon,lat = extract_coordinates(dataframe['stop_lat'][i],dataframe['stop_lon'][i])
        
        station_positions[dataframe['stop_id'][i]] = lon,lat

        #Get current station name
        station_name_labels[dataframe['stop_id'][i]] = [dataframe['stop_name'][i]][0]

        #Getting nodes (departure, arrival)
        departure, arrival = dataframe['stop_id'][i-1], dataframe['stop_id'][i]

        #Calculating time difference, aka weights
        previous_arrival_time, arrival_time = dataframe['arrival_time'][i-1],dataframe['arrival_time'][i]
        time_difference = calculate_time_difference(time1= previous_arrival_time, time2= arrival_time)

        #Adding edges with weights (starting node, ending node, weight)
        edges.append((departure,arrival,time_difference))

        #Adding edge labels
        edge_labels[(departure,arrival)] = [dataframe['route_short_name'][i]][0]

        #Adding edge colors
        edge_colors.append(('#'+[dataframe['route_color'][i]][0]))
        
        node_labels[dataframe['stop_id'][i]] = {'name': [dataframe['stop_name'][i]][0],'lon': lon,'lat': lat}
    
    #Return values: station name labels (node labels), edges, edge labels, edge colors, node positions, node attributes
    return (station_name_labels,edges,edge_labels,edge_colors,station_positions,node_labels)

### Building network

In [ ]:
G = nx.Graph()

#station_name_labels,edges,edge_labels,edge_colors

station_name_labels = {}
station_node_positions = {}
edges = []
edge_labels = {}
edge_colors = []
all_node_attributes = {}

for trip_id in unique_trip_ids:
    trip_data = (dataset.loc[dataset['trip_id'] == trip_id]).sort_values('arrival_time')
    trip_data.reset_index(drop=True, inplace=True)
    
    res = generate_data_for_network(trip_data)
    station_name_labels.update(res[0])
    edges.extend(res[1])
    edge_labels.update(res[2])
    edge_colors.extend(res[3])
    station_node_positions.update(res[4])
    all_node_attributes.update(res[5])


In [ ]:
G.add_weighted_edges_from(edges);
nx.set_node_attributes(G, all_node_attributes)

### Removing duplicated stations

In [ ]:
nodekeys = list(G.nodes.keys())

#Getting unique names
names = []
for node_id in nodekeys:
    names.append(G.nodes[node_id]['name'])
names = list(set(names))

nodes_to_merge = []
for unique_stop_name in names:
    multiple_stops_with_same_name = []
    for stop_id, data in G.nodes.items():
        current_name = data['name']
        if current_name == unique_stop_name:
            multiple_stops_with_same_name.append((stop_id,current_name,data['lon'],data['lat']))
    same_named_stops = []
    if len(multiple_stops_with_same_name) == 1: # station is not duplicated
        continue
    for row in multiple_stops_with_same_name:
        if not same_named_stops: #list is empty
            same_named_stops.append([(row[0],row[3],row[2])])
        else:
            could_find_place = False
            current_node = (row[0],row[3],row[2])
            for already_saved_nodes in same_named_stops:
                is_close = check_whether_node_isclose(nodes= already_saved_nodes,new_node= current_node)
                if is_close:
                    already_saved_nodes.append(current_node)
                    could_find_place = True
                    break
            if not could_find_place:
                same_named_stops.append([current_node])
                    
    if len(same_named_stops) > 0:
        nodes_to_merge.append(same_named_stops)

In [ ]:
#Merging nodes
for same_name_nodes in nodes_to_merge:
    for same_name in same_name_nodes:
        if len(same_name) > 1:
            base_node_key = same_name[0][0]
            for i in range(1,len(same_name)):
                key = str(same_name[i][0])
                G = nx.contracted_nodes(G, base_node_key, key)

In [ ]:
#Removing unused node labels, node positions, edge labels
filtered_labels = {}
filtered_station_node_positions = {}
filtered_edge_labels = {}
for label_key, label in station_name_labels.items():
    if label_key in G.nodes:
        filtered_labels[label_key] = label
        
for pos_key, pos in station_node_positions.items():
    if pos_key in G.nodes:
        filtered_station_node_positions[pos_key] = pos

for k,v in edge_labels.items():
    if k[0] in G.nodes and k[1] in G.nodes:
        filtered_edge_labels[k] = v
        

### Exporting graph with pickle

In [ ]:
#Dumping network object
savename = 'bkk_random_network.dat'
with open(savename, "wb") as f:
    pickle.dump((G,filtered_station_node_positions,filtered_labels,edge_colors,filtered_edge_labels), f)

## Loading exported data

In [8]:
with open('bkk_morning_network.dat', "rb") as raw_network_data_file_morning:
    raw_network_data_morning = pickle.load(raw_network_data_file_morning)
with open('bkk_evening_network.dat', "rb") as raw_network_data_file_evening:
    raw_network_data_evening = pickle.load(raw_network_data_file_evening)
with open('bkk_day_network.dat', "rb") as raw_network_data_file_day:
    raw_network_data_day = pickle.load(raw_network_data_file_day)
with open('bkk_random_network.dat', "rb") as raw_network_data_file_random:
    raw_network_data_random = pickle.load(raw_network_data_file_random)

In [20]:
G_morning, morning_filtered_station_node_positions, morning_filtered_labels, morning_edge_colors, morning_filtered_edge_labels = raw_network_data_morning
G_evening, evening_filtered_station_node_positions, evening_filtered_labels, evening_edge_colors, evening_filtered_edge_labels = raw_network_data_evening
G_day, day_filtered_station_node_positions, day_filtered_labels, day_edge_colors, day_filtered_edge_labels = raw_network_data_day
G_random, day_filtered_station_node_positions, day_filtered_labels, day_edge_colors, day_filtered_edge_labels = raw_network_data_random

In [13]:
#Displaying network, saving to PDF
fig = plt.figure(figsize=(140,140))
nx.draw(G_morning,pos=morning_filtered_station_node_positions,labels = morning_filtered_labels,font_size=7, edge_color= morning_edge_colors,node_size=25)
nx.draw_networkx_edge_labels(G_morning,morning_filtered_station_node_positions,edge_labels=morning_filtered_edge_labels,font_size=7,font_color='red')

plt.axis('off')
#plt.show()
plt.savefig('bkk_network_morning.pdf')

## Time calculation function

In [41]:
def time_calculation(root,G):
    path_edges = list(nx.bfs_edges(G, root))
    edges_list = list(G.edges(data=True))
    path_sum = 0
    for edge in edges_list:
        for path_edge in path_edges:
            if (edge[0] == path_edge[0] and edge[1] == path_edge[1]) or (edge[0] == path_edge[1] and edge[1] == path_edge[0]):
                path_sum += int(edge[2]['weight'])
    return path_sum

## Morning Graph

In [42]:
morning_path_length = time_calculation('045755',G_morning)

## Afternoon Graph

In [43]:
afternoon_path_length = time_calculation('045755',G_day)

## Evening Graph

In [44]:
evening_path_length = time_calculation('045755',G_evening)

## Random Graph

In [45]:
random_path_length = time_calculation('045755',G_random)

## Table to show the time in seconds and hours for each network

In [46]:
from prettytable import PrettyTable

x = PrettyTable(["Graphs", "In seconds", "In hours"])

x.add_row(["Morning", morning_path_length, morning_path_length/3600])
x.add_row(["Evening", evening_path_length, evening_path_length/3600])
x.add_row(["Afternoon", afternoon_path_length, afternoon_path_length/3600])
x.add_row(["Random", random_path_length, random_path_length/3600])

print(x.get_string())

+-----------+------------+--------------------+
|   Graphs  | In seconds |      In hours      |
+-----------+------------+--------------------+
|  Morning  |   183980   | 51.105555555555554 |
|  Evening  |   174170   | 48.38055555555555  |
| Afternoon |   205305   | 57.02916666666667  |
|   Random  |   207220   | 57.56111111111111  |
+-----------+------------+--------------------+
